$$Logic Regression


In [1]:
!pip install pandas --quiet
!pip install scikit-learn --quiet
!pip install numpy --quiet
import pandas as pd
import numpy as np


In [2]:
raw_df = pd.read_csv('weatherAUS.csv')
raw_df.head()

Date Location  MinTemp  MaxTemp  Rainfall  Evaporation  Sunshine  \
0  2008-12-01   Albury     13.4     22.9       0.6          NaN       NaN   
1  2008-12-02   Albury      7.4     25.1       0.0          NaN       NaN   
2  2008-12-03   Albury     12.9     25.7       0.0          NaN       NaN   
3  2008-12-04   Albury      9.2     28.0       0.0          NaN       NaN   
4  2008-12-05   Albury     17.5     32.3       1.0          NaN       NaN   

  WindGustDir  WindGustSpeed WindDir9am  ... Humidity9am  Humidity3pm  \
0           W           44.0          W  ...        71.0         22.0   
1         WNW           44.0        NNW  ...        44.0         25.0   
2         WSW           46.0          W  ...        38.0         30.0   
3          NE           24.0         SE  ...        45.0         16.0   
4           W           41.0        ENE  ...        82.0         33.0   

   Pressure9am  Pressure3pm  Cloud9am  Cloud3pm  Temp9am  Temp3pm  RainToday  \
0       1007.7       1007.1       8.0       NaN     16.9     21.8         No   
1       1010.6       1007.8       NaN       NaN     17.2     24.3         No   
2       1007.6       1008.7       NaN       2.0     21.0     23.2         No   
3       1017.6       1012.8       NaN       NaN     18.1     26.5         No   
4       1010.8       1006.0       7.0       8.0     17.8     29.7         No   

   RainTomorrow  
0            No  
1            No  
2            No  
3            No  
4            No  

[5 rows x 23 columns]

In [3]:
raw_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 145460 entries, 0 to 145459
Data columns (total 23 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   Date           145460 non-null  object 
 1   Location       145460 non-null  object 
 2   MinTemp        143975 non-null  float64
 3   MaxTemp        144199 non-null  float64
 4   Rainfall       142199 non-null  float64
 5   Evaporation    82670 non-null   float64
 6   Sunshine       75625 non-null   float64
 7   WindGustDir    135134 non-null  object 
 8   WindGustSpeed  135197 non-null  float64
 9   WindDir9am     134894 non-null  object 
 10  WindDir3pm     141232 non-null  object 
 11  WindSpeed9am   143693 non-null  float64
 12  WindSpeed3pm   142398 non-null  float64
 13  Humidity9am    142806 non-null  float64
 14  Humidity3pm    140953 non-null  float64
 15  Pressure9am    130395 non-null  float64
 16  Pressure3pm    130432 non-null  float64
 17  Cloud9am       89572 non-null

In [4]:
# remove null values rows
raw_df.dropna(subset=['RainTomorrow','RainTomorrow'], inplace=True)
raw_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 142193 entries, 0 to 145458
Data columns (total 23 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   Date           142193 non-null  object 
 1   Location       142193 non-null  object 
 2   MinTemp        141556 non-null  float64
 3   MaxTemp        141871 non-null  float64
 4   Rainfall       140787 non-null  float64
 5   Evaporation    81350 non-null   float64
 6   Sunshine       74377 non-null   float64
 7   WindGustDir    132863 non-null  object 
 8   WindGustSpeed  132923 non-null  float64
 9   WindDir9am     132180 non-null  object 
 10  WindDir3pm     138415 non-null  object 
 11  WindSpeed9am   140845 non-null  float64
 12  WindSpeed3pm   139563 non-null  float64
 13  Humidity9am    140419 non-null  float64
 14  Humidity3pm    138583 non-null  float64
 15  Pressure9am    128179 non-null  float64
 16  Pressure3pm    128212 non-null  float64
 17  Cloud9am       88536 non-null   fl

In [5]:
try:  import plotly.express as px
except ModuleNotFoundError:
    %pip install plotly
    import plotly.express as px

px.histogram(raw_df, x='Location' , title="Location vs. RainyDays",color = 'RainToday')

In [6]:
px.histogram(raw_df,x='Temp3pm',title='Temperature at 3pm', color='RainTomorrow')

Set sample


In [7]:
use_sample = False 
sample_fraction = 0.1
if use_sample:
    raw_df = raw_df.sample(frac=sample_fraction.copy())

In [8]:
from sklearn.model_selection import train_test_split


In [9]:
train_val_df, test_df = train_test_split(raw_df, test_size=0.2, random_state=42)
train_df, val_df = train_test_split(train_val_df, test_size=0.25, random_state=42) # 0.25 x 0.8 = 0.2


In [10]:
print(f"Train set: {train_df.shape}")
print(f"Validation set: {val_df.shape}")
print(f"Test set: {test_df.shape}")

Train set: (85315, 23)
Validation set: (28439, 23)
Test set: (28439, 23)


In [11]:
# to make the accuracy in predication use to the technique where we use data till 2017 as the training data and after 2015 as the testing data
year  = pd.to_datetime(raw_df.Date).dt.year
train_df = raw_df[year <= 2015]
val_df = raw_df[year == 2015]
test_df = raw_df[year > 2015]

#Identifying Input & target Columns


In [12]:
input_cols = list(train_df.columns)[1:-1] #ignore date col
target_col = 'RainTomorrow' #output col




In [13]:
numeric_cols = train_df[input_cols].select_dtypes(include=np.number).columns.tolist()  # Exclude target column if numeric
categorical_cols = train_df[input_cols].select_dtypes(include='object').columns.tolist()

In [14]:
train_inputs = train_df[numeric_cols].describe()
train_inputs

MinTemp        MaxTemp       Rainfall   Evaporation  \
count  115742.000000  115990.000000  115077.000000  70646.000000   
mean       12.032410      23.077370       2.337669      5.367306   
std         6.375807       7.065463       8.483712      4.048918   
min        -8.500000      -4.100000       0.000000      0.000000   
25%         7.500000      17.900000       0.000000      2.600000   
50%        11.800000      22.500000       0.000000      4.600000   
75%        16.700000      28.000000       0.600000      7.200000   
max        33.900000      48.100000     371.000000     82.400000   

           Sunshine  WindGustSpeed   WindSpeed9am   WindSpeed3pm  \
count  66358.000000  108409.000000  115004.000000  114709.000000   
mean       7.619633      40.131853      14.061120      18.721983   
std        3.781878      13.607206       8.948117       8.857876   
min        0.000000       6.000000       0.000000       0.000000   
25%        4.900000      31.000000       7.000000      13.000000   
50%        8.500000      39.000000      13.000000      19.000000   
75%       10.600000      48.000000      19.000000      24.000000   
max       14.500000     135.000000      87.000000      87.000000   

         Humidity9am    Humidity3pm    Pressure9am    Pressure3pm  \
count  114733.000000  114365.000000  104885.000000  104923.000000   
mean       68.579118      51.350964    1017.750217    1015.358392   
std        19.130313      20.801623       7.103810       7.036906   
min         0.000000       0.000000     980.500000     979.000000   
25%        57.000000      37.000000    1013.000000    1010.600000   
50%        70.000000      52.000000    1017.700000    1015.300000   
75%        83.000000      65.000000    1022.500000    1020.100000   
max       100.000000     100.000000    1041.000000    1039.600000   

           Cloud9am      Cloud3pm        Temp9am        Temp3pm  
count  73862.000000  72434.000000  115405.000000  115078.000000  
mean       4.334001      4.427658      16.868786      21.579581  
std        2.876184      2.705274       6.463913       6.898924  
min        0.000000      0.000000      -6.200000      -5.100000  
25%        1.000000      2.000000      12.200000      16.600000  
50%        5.000000      5.000000      16.600000      21.000000  
75%        7.000000      7.000000      21.400000      26.300000  
max        9.000000      9.000000      40.200000      46.100000

In [15]:
train_df[categorical_cols].nunique()

Location       49
WindGustDir    16
WindDir9am     16
WindDir3pm     16
RainToday       2
dtype: int64

$Inputing 
The process of filling missing values is called imputation 

In [16]:
# fill average value
from sklearn.impute import SimpleImputer
imputer = SimpleImputer(strategy='mean')

before imputation lets check the no. of missing values in each numeric column

In [17]:
raw_df[numeric_cols].isna().sum()

MinTemp            637
MaxTemp            322
Rainfall          1406
Evaporation      60843
Sunshine         67816
WindGustSpeed     9270
WindSpeed9am      1348
WindSpeed3pm      2630
Humidity9am       1774
Humidity3pm       3610
Pressure9am      14014
Pressure3pm      13981
Cloud9am         53657
Cloud3pm         57094
Temp9am            904
Temp3pm           2726
dtype: int64

In [18]:
train_df[numeric_cols] = imputer.fit_transform(train_df[numeric_cols])
val_df[numeric_cols] = imputer.transform(val_df[numeric_cols])
test_df[numeric_cols] = imputer.transform(test_df[numeric_cols]) 

/tmp/ipykernel_103640/2166986698.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_103640/2166986698.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_103640/2166986698.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



$$Scaler


In [19]:
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()
scaler.fit(raw_df[numeric_cols])

MinMaxScaler()

In [20]:
scaler.fit(raw_df[numeric_cols])

MinMaxScaler()

In [21]:
train_df[numeric_cols] = scaler.transform(train_df[numeric_cols])
val_df[numeric_cols] = scaler.transform(val_df[numeric_cols])
test_df[numeric_cols] = scaler.transform(test_df[numeric_cols])

/tmp/ipykernel_103640/3660065040.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_103640/3660065040.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_103640/3660065040.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



$$Encoding

In [22]:
raw_df[categorical_cols].nunique()

Location       49
WindGustDir    16
WindDir9am     16
WindDir3pm     16
RainToday       2
dtype: int64

In [23]:
from sklearn.preprocessing import OneHotEncoder
encoder = OneHotEncoder(sparse_output=False, handle_unknown='ignore')
encoder.fit(raw_df[categorical_cols])
encoded_cols = list(encoder.get_feature_names_out(categorical_cols))
train_df[encoded_cols] = encoder.transform(train_df[categorical_cols])
val_df[encoded_cols] = encoder.transform(val_df[categorical_cols])
test_df[encoded_cols] = encoder.transform(test_df[categorical_cols])


/tmp/ipykernel_103640/2751385899.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_103640/2751385899.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_103640/2751385899.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykerne

$$Pyarrow_Format

In [24]:
!pip install pyarrow --quiet

In [25]:

train_df.to_parquet('train_inputs.parquet')
val_df.to_parquet('val_inputs.parquet')
test_df.to_parquet('test_inputs.parquet')

In [26]:
pd.DataFrame(train_df).to_parquet('train_inputs.parquet')
pd.DataFrame(val_df).to_parquet('val_inputs.parquet')   
pd.DataFrame(test_df).to_parquet('test_inputs.parquet') 